In [5]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import openai
import json
import ijson
from retrying import retry
import os
import requests
from pywikidata import Entity

openai.api_key = os.getenv("KEY")

openai.base_url = "https://api.vsegpt.ru:6070/v1/"

In [7]:
@retry(stop_max_attempt_number=3, wait_fixed=20000)  # Retry 3 times with a fixed delay of 2 seconds
def send_request(question_text):
    url = 'http://5.35.10.151:8080/pipeline/act_selection/main'  # Replace with your server's IP address and port
    headers = {'Content-Type': 'application/json'}
    data = {'text': question_text}

    response = requests.post(url, json=data, headers=headers)

    if response.status_code == 200 or response.status_code == 307:
        return response.json()  # Assuming the response is in JSON format
    else:
        print(f"Error: {response.status_code}")
        raise Exception

In [2]:
file_path = "mintaka_test.json"
with open(file_path, 'r') as file:
    array_items = ijson.items(file, 'item')
    
    i = 0
    true_answers = 0
    answers = []
    for item in array_items:
        messages = []
        i += 1

        question = item["question"]
        print(item)
        if item["answer"]["answerType"] == "entity":
            if item["answer"]["answer"]:
                answer = item["answer"]["answer"][0]["label"]['en']
            else:
                answer = ""
        else:
            if len(item["answer"]["answer"]):
                answer = str(item["answer"]["answer"][0])
            else:
                answer = ""

        prompt = "Answer shortly in 1-3 words. If answer is a number, print digits"
        # prompt = "Ответь максимально коротко и ёмко на вопрос. Ответ приводи в именительном падеже, при этом не забывай о пунктуации."
        # messages.append({"role": "user", "content": prompt})
        messages.append({"role": "user", "content": prompt + ' ' + question})
        response = ""
        try:
            response_big = openai.chat.completions.create(
                model="openai/gpt-3.5-turbo-1106",
                messages=messages,
                temperature=0.1,
            )
        except:
            continue
        response = response_big.choices[0].message.content.lower()
        answers.append({
            "question": question,
            "answer": response,
            "correct_answer": answer.lower(),
            "is_correct": answer.lower() in response
        })
        if answer.lower() in response:
            true_answers += 1
        print(i, true_answers)
        json_data = json.dumps(answers, indent=4)
        with open("questions_answers_mintaka.json", "w") as json_file:
            json_file.write(json_data)

{'id': 'fae46b21', 'question': 'What man was a famous American author and also a steamboat pilot on the Mississippi River?', 'translations': {'ar': 'مَن الرجل الذي كان مؤلفًا أمريكيًا مشهورًا وعمل أيضًا كقبطان لباخرة على نهر المسيسيبي؟', 'de': 'Wer war ein berühmter amerikanischer Schriftsteller und gleichzeitig ein Dampfschifflotse auf dem Mississippi?', 'ja': 'アメリカの有名な作家でミシシッピ川の蒸気船のパイロットだった男は誰ですか？', 'hi': 'प्रमुख अमेरिकन लेखक और साथ ही मिसिसिप्पी नदी में एक स्ट्रीमबोट पायलट कौन हैं?', 'pt': 'Qual homem foi um autor americano famoso e também um piloto de barco a vapor no rio Mississippi?', 'es': '¿Qué hombre fue un autor famoso estadounidense y también piloto de barcos de vapor en el río Misisipi?', 'it': 'Chi fu un celebre autore americano e anche pilota di battelli a vapore sul Mississippi?', 'fr': 'Quel célèbre auteur américain était aussi pilote de navire à vapeur sur le fleuve du Mississippi ?'}, 'questionEntity': [{'name': 'Q1497', 'entityType': 'entity', 'label': 'Mississippi R

In [9]:
file_path = "mintaka_test.json"
with open(file_path, 'r') as file:
    array_items = ijson.items(file, 'item')
    
    i = 0
    true_answers = 0
    answers = []
    for item in array_items:
        messages = []
        i += 1

        question = item["question"]
        if item["answer"]["answerType"] == "entity":
            if item["answer"]["answer"]:
                answer = item["answer"]["answer"][0]["label"]['en']
            else:
                answer = ""
        else:
            if len(item["answer"]["answer"]):
                answer = str(item["answer"]["answer"][0])
            else:
                answer = ""

        response = ""
        try:
            response_data = send_request(question)
            response = Entity(response_data['answers'][0]).label.lower()
        except:
            response = ""
        answers.append({
            "question": question,
            "answer": response,
            "correct_answer": answer.lower(),
            "is_correct": answer.lower() in response
        })
        if answer.lower() in response:
            true_answers += 1
        print(i, true_answers)
        json_data = json.dumps(answers, indent=4)
        with open("questions_answers_mintaka.json", "w") as json_file:
            json_file.write(json_data)

1 0
Error: 500
Error: 500
Error: 500
2 0
3 0
4 0
5 0
6 1
Error: 500
Error: 500
Error: 500
7 1
8 1
Error: 500
Error: 500
Error: 500
9 1
10 1
11 1
12 1
13 1
14 1
Error: 500
Error: 500
Error: 500
15 1
16 1
17 1
18 1
19 1
Error: 500
Error: 500
Error: 500
20 1
Error: 500
Error: 500
Error: 500
21 1
22 1
23 1
Error: 500
24 1
25 1
26 1
Error: 500
Error: 500
Error: 500
27 1
Error: 500
Error: 500
Error: 500
28 1
29 1
30 1
31 2
Error: 500
Error: 500
Error: 500
32 2
33 2
34 3
35 3
Error: 500
Error: 500
Error: 500
36 3
Error: 500
Error: 500
Error: 500
37 3
Error: 500
Error: 500
Error: 500
38 3
Error: 500
Error: 500
Error: 500
39 3
Error: 500
Error: 500
Error: 500
40 3
Error: 500
Error: 500
Error: 500
41 3
42 3
43 3
44 3
45 3
46 3
47 3
Error: 500
Error: 500
Error: 500
48 3
Error: 500
Error: 500
Error: 500
49 3
50 3
51 3
52 3
Error: 500
Error: 500
Error: 500
53 3
Error: 500
Error: 500
Error: 500
54 3
55 3
Error: 500
Error: 500
Error: 500
56 3
57 3
58 3
Error: 500
Error: 500
Error: 500
59 3
60 3
61 3
